In [35]:
import serial
from bokeh.io import push_notebook, show, output_notebook
from bokeh.models import HoverTool, Range1d
from bokeh.plotting import figure 
output_notebook()

Loading BokehJS ...

In [36]:
import chipwhisperer as cw

#connect to chipwhisperer
scope = cw.scope()
target = cw.target(scope)

In [37]:
# setup scope parameters
NUMBER_OF_SAMPLES = 24400 # first aees round
scope.gain.gain = 45
scope.adc.samples = NUMBER_OF_SAMPLES 
scope.adc.offset = 0
scope.adc.basic_mode = "high"
scope.clock.clkgen_freq = 16000000
scope.clock.adc_src = "clkgen_x4"
scope.trigger.triggers = "tio4"
scope.io.tio1 = "serial_rx"
scope.io.tio2 = "serial_tx"
scope.io.hs2 = "clkgen"

In [38]:
# external serial port used because chipwhisperer's not working for some reason (to be investigated)
ser = serial.Serial('/dev/ttyUSB1', 115200, timeout=100)
ser.close()
ser.open()

In [39]:
#Capture Traces
from tqdm import tqdm
from chipwhisperer.capture.acq_patterns.basic import AcqKeyTextPattern_Basic
import numpy as np
import time

encryption_suite = AES.new(bytes.fromhex('2b7e151628aed2a6abf7158809cf4f3c'), AES.MODE_ECB)
ktp = AcqKeyTextPattern_Basic(target=target)

traces = []
textin = []
keys = []
N = 500  # Number of traces
target.init()

target.key_cmd = ""
target.go_cmd = ""
target.output_cmd = ""

x = np.arange(NUMBER_OF_SAMPLES)
y = np.zeros(NUMBER_OF_SAMPLES)

p = figure()
p.y_range=Range1d(-0.2, 0.2)

trace_plot = p.line(x,y)
target_plot = show(p, notebook_handle=True)

for i in tqdm(range(N), desc='Capturing traces'):
    # run aux stuff that should come before trace here

    key, text = ktp.newPair()  # manual creation of a key, text pair can be substituted here
    # override key because one is supported currently
    key = bytearray(b'\x2b\x7e\x15\x16\x28\xae\xd2\xa6\xab\xf7\x15\x88\x09\xcf\x4f\x3c')
    
    textin.append(text)
    keys.append(key)

    scope.arm()

    # trigger encryption:
    ser.write(text)
    
    timeout = 50
    # wait for target to finish
    while target.isDone() is False and timeout:
        timeout -= 1
        time.sleep(0.01)

    try:
        ret = scope.capture()
        if ret:
            print('Timeout happened during acquisition')
    except IOError as e:
        print('IOError: %s' % str(e))
    
    encrypted = ser.read(16)
    cipher_text = encryption_suite.encrypt(bytes.fromhex(text.hex()))

    # exit if something went wrong:
    if bytearray(cipher_text) != encrypted:
        print("abort after {} iterations because of wrong encryption result".format(i))
        break
        
    # run aux stuff that should happen after trace here
    trace = scope.getLastTrace()
    traces.append(trace)
    
    trace_plot.data_source.data['y'] = trace
    push_notebook(handle=target_plot)

#Convert traces to numpy arrays
trace_array = np.asarray(traces)  # if you prefer to work with numpy array for number crunching
textin_array = np.asarray(textin)
known_keys = np.asarray(keys)  # for fixed key, these keys are all the same

Capturing traces: 100%|██████████| 500/500 [01:20<00:00,  6.26it/s]


In [40]:
# cleanup the connection to the target and scope
scope.dis()
target.dis()

In [78]:
from __future__ import division, print_function

import numpy as np
from tqdm import tqdm

sbox = (
    0x63, 0x7c, 0x77, 0x7b, 0xf2, 0x6b, 0x6f, 0xc5, 0x30, 0x01, 0x67, 0x2b, 0xfe, 0xd7, 0xab, 0x76,
    0xca, 0x82, 0xc9, 0x7d, 0xfa, 0x59, 0x47, 0xf0, 0xad, 0xd4, 0xa2, 0xaf, 0x9c, 0xa4, 0x72, 0xc0,
    0xb7, 0xfd, 0x93, 0x26, 0x36, 0x3f, 0xf7, 0xcc, 0x34, 0xa5, 0xe5, 0xf1, 0x71, 0xd8, 0x31, 0x15,
    0x04, 0xc7, 0x23, 0xc3, 0x18, 0x96, 0x05, 0x9a, 0x07, 0x12, 0x80, 0xe2, 0xeb, 0x27, 0xb2, 0x75,
    0x09, 0x83, 0x2c, 0x1a, 0x1b, 0x6e, 0x5a, 0xa0, 0x52, 0x3b, 0xd6, 0xb3, 0x29, 0xe3, 0x2f, 0x84,
    0x53, 0xd1, 0x00, 0xed, 0x20, 0xfc, 0xb1, 0x5b, 0x6a, 0xcb, 0xbe, 0x39, 0x4a, 0x4c, 0x58, 0xcf,
    0xd0, 0xef, 0xaa, 0xfb, 0x43, 0x4d, 0x33, 0x85, 0x45, 0xf9, 0x02, 0x7f, 0x50, 0x3c, 0x9f, 0xa8,
    0x51, 0xa3, 0x40, 0x8f, 0x92, 0x9d, 0x38, 0xf5, 0xbc, 0xb6, 0xda, 0x21, 0x10, 0xff, 0xf3, 0xd2,
    0xcd, 0x0c, 0x13, 0xec, 0x5f, 0x97, 0x44, 0x17, 0xc4, 0xa7, 0x7e, 0x3d, 0x64, 0x5d, 0x19, 0x73,
    0x60, 0x81, 0x4f, 0xdc, 0x22, 0x2a, 0x90, 0x88, 0x46, 0xee, 0xb8, 0x14, 0xde, 0x5e, 0x0b, 0xdb,
    0xe0, 0x32, 0x3a, 0x0a, 0x49, 0x06, 0x24, 0x5c, 0xc2, 0xd3, 0xac, 0x62, 0x91, 0x95, 0xe4, 0x79,
    0xe7, 0xc8, 0x37, 0x6d, 0x8d, 0xd5, 0x4e, 0xa9, 0x6c, 0x56, 0xf4, 0xea, 0x65, 0x7a, 0xae, 0x08,
    0xba, 0x78, 0x25, 0x2e, 0x1c, 0xa6, 0xb4, 0xc6, 0xe8, 0xdd, 0x74, 0x1f, 0x4b, 0xbd, 0x8b, 0x8a,
    0x70, 0x3e, 0xb5, 0x66, 0x48, 0x03, 0xf6, 0x0e, 0x61, 0x35, 0x57, 0xb9, 0x86, 0xc1, 0x1d, 0x9e,
    0xe1, 0xf8, 0x98, 0x11, 0x69, 0xd9, 0x8e, 0x94, 0x9b, 0x1e, 0x87, 0xe9, 0xce, 0x55, 0x28, 0xdf,
    0x8c, 0xa1, 0x89, 0x0d, 0xbf, 0xe6, 0x42, 0x68, 0x41, 0x99, 0x2d, 0x0f, 0xb0, 0x54, 0xbb, 0x16)

def intermediate(pt, keyguess):
    return sbox[pt ^ keyguess]

HW = [bin(n).count("1") for n in range(0, 256)]

numtraces = np.shape(trace_array)[0] #total number of traces
numpoint = np.shape(trace_array)[1] #samples per trace

pt = textin_array
traces = trace_array
knownkey = known_keys[0]
cparefs = [0] * 16
bestguess = [0]*16

cpaoutput = np.zeros((16, 256, NUMBER_OF_SAMPLES))
for bnum in tqdm(range(0, 16), desc='Attacking subkeys'):
    maxcpa = [0] * 256
    for kguess in range(0, 256):

        # Initialize arrays &amp; variables to zero
        sumnum = np.zeros(numpoint)
        sumden1 = np.zeros(numpoint)
        sumden2 = np.zeros(numpoint)

        hyp = np.zeros(numtraces)
        for tnum in range(0, numtraces):
            hyp[tnum] = HW[intermediate(pt[tnum][bnum], kguess)]

        # Mean of hypothesis
        meanh = np.mean(hyp, dtype=np.float64)

        # Mean of all points in trace
        meant = np.mean(traces, axis=0, dtype=np.float64)

        # For each trace, do the following
        for tnum in range(0, numtraces):
            hdiff = (hyp[tnum] - meanh)
            tdiff = traces[tnum, :] - meant

            sumnum = sumnum + (hdiff * tdiff)
            sumden1 = sumden1 + hdiff * hdiff
            sumden2 = sumden2 + tdiff * tdiff

        cpaoutput[bnum, kguess, :] = sumnum / np.sqrt(sumden1 * sumden2)
        maxcpa[kguess] = max(abs(cpaoutput[bnum, kguess, :]))

    bestguess[bnum] = np.argmax(maxcpa)
    cparefs[bnum] = np.argsort(maxcpa)[::-1]

print("Best Key Guess: ", end="")
for b in bestguess: print("%02x " % b, end="")

Attacking subkeys: 100%|██████████| 16/16 [04:02<00:00, 15.11s/it]

Best Key Guess: 2b 7e 15 16 28 ae d2 a6 ab f7 15 88 09 cf 4f 3c 

In [79]:
for b in knownkey: print("%02x "%b, end="")
print("\n")
if (knownkey == bestguess).all():
    print("Guess was right")
else:
    print("Guess was wrong")

2b 7e 15 16 28 ae d2 a6 ab f7 15 88 09 cf 4f 3c 

Guess was right


In [86]:
from bokeh.palettes import Category20b

p = figure(plot_width=1000)

for i, b in enumerate(knownkey):
    p.line(np.arange(NUMBER_OF_SAMPLES), cpaoutput[i, b, :], color=Category20b[16][i])

p.y_range=Range1d(-1, 1)
p.x_range=Range1d(0, NUMBER_OF_SAMPLES)

show(p)